# Binary classification with the crabs data

In this example we show how the GP Monte Carlo function can be used for supervised learning classification. We use the Crab dataset from the R package MASS. In this dataset we are interested in predicting whether a crab is of colour form blue or orange.

In [1]:
using GaussianProcesses

train=readdlm("data/crabs_train.txt",',');

train[train[:,1].==-1.0,1]=0.0;
y = convert(Vector{Bool},train[:,1]);       # response
X = train[:,2:end];                         # predictors

We assume a zero mean GP with a Matern 3/2 kernel. We use the automatic relevance determination (ARD) kernel to allow each dimension of the predictor variables to have a different length scale. As this is binary classifcation, we use the Bernoulli likelihood.

In [2]:
#Select mean, kernel and likelihood function
mZero = MeanZero()   #Zero mean function
kern = Matern(3/2,zeros(5),0.0)   #Matern 3/2 ARD kernel (note that hyperparameters are on the log scale)
lik = BernLik()

Type: GaussianProcesses.BernLik, Params: Any[]


We fit the GP using the general `GP` function. This function is a shorthand for the `GPMC` function which is used to generate Monte Carlo approximations of the latent function when the likelihood is non-Gaussian. 

In [3]:
gp = GP(X',vec(y),mZero,kern,lik)

GP Monte Carlo object:
  Dim = 5
  Number of observations = 100
  Mean function:
    Type: GaussianProcesses.MeanZero, Params: Float64[]
  Kernel:
    Type: GaussianProcesses.Mat32Ard, Params: [-0.0,-0.0,-0.0,-0.0,-0.0,0.0]
  Likelihood:
    Type: GaussianProcesses.BernLik, Params: Any[]
  Input observations = 
[8.1 8.8 … 17.5 19.2; 6.7 7.7 … 16.7 16.5; … ; 19.0 20.8 … 44.5 47.9; 7.0 7.4 … 17.0 18.1]
  Output observations = Bool[false,false,false,false,false,false,false,false,false,false  …  true,true,true,true,true,true,true,true,true,true]
  Log-posterior = -161.209

In [4]:
We assign `Normal` priors from the `Distributions` package to each of the Matern 3/2 kernel parameters.

LoadError: syntax: extra token "assign" after end of expression

In [5]:
set_priors!(gp.k,[Distributions.Normal(0.0,2.0) for i in 1:6])

6-element Array{Distributions.Normal{Float64},1}:
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)

Samples of the latent function $f|X,y,\theta$ are drawn using MCMC sampling. The MCMC routine uses the `Klara` package. By default, the `mcmc` function uses the MALA algorithm, where the stepsize is automatically tuned to a desired acceptance rate. Alternative samplers, such as HMC and NUTS, can also be used. 

In [6]:
samples = mcmc(gp)

BasicMCJob:
  Variable [1]: p (Klara.BasicContMuvParameter)
  GenericModel: 1 variables, 0 dependencies (directed graph)
  MALA sampler: drift step = 0.1
  VanillaMCTuner: period = 100, verbose = false
  BasicMCRange: number of steps = 5000, burnin = 1000, thinning = 1
  plain = true (job flow not controlled by tasks)

106×4000 Array{Float64,2}:
  0.0218528    0.256832     0.256832    …  -0.302273   -0.302273   -0.302273 
 -0.684932    -0.429229    -0.429229       -0.149953   -0.149953   -0.149953 
  0.437747     0.44674      0.44674         0.287418    0.287418    0.287418 
  0.177475    -0.00499257  -0.00499257     -0.38544    -0.38544    -0.38544  
  0.00438975   0.187532     0.187532        0.876611    0.876611    0.876611 
 -1.0175      -1.13479     -1.13479     …   0.0531735   0.0531735   0.0531735
  0.333472     0.382272     0.382272       -0.582206   -0.582206   -0.582206 
 -1.3892      -1.45687     -1.45687        -1.12528    -1.12528    -1.12528  
  0.523746     0.125239     0.125239       -0.551809   -0.551809   -0.551809 
  0.269302     0.913518     0.913518        0.0344306   0.0344306   0.0344306
 -0.442526    -1.04142     -1.04142     …  -0.442074   -0.442074   -0.442074 
  0.16869      0.1078       0.1078          1.51187     1.51187     1.51187  
 -0.328974    -0.463307    -0.463307 

We test the predictive accuracy of the fitted model against a hold-out dataset

In [7]:
test = readdlm("data/crabs_test.txt",',');
test[test[:,1].==-1.0,1]=0.0;

xTest = test[:,2:end];
yTest = test[:,1];

In [8]:
ymean = Array(Float64,size(samples,2),size(xTest,1));

for i in 1:size(samples,2)
    set_params!(gp,samples[:,i])
    update_target!(gp)
    ymean[i,:] = predict_y(gp,xTest')[1]
end

In [9]:
using Plots
gr()

plot(ymean',leg=false)
scatter!(yTest)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0 
 
 
 50 
 
 
 100 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
<polyline clip-path="url(#clip02)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 55.0141,243.831 60.2815,224.069 65.5488,184.083 70.8162,337.452 76.0835,336.292 81.3509,351.501 86.6182,316.978 91.8856,311.559 97.1529,337.329 102.42,320.793 
 107.688,295.684 112.955,351.758 118.222,353.097 123.49,353.461 128.757,352.706 134.024,344.631 139.292,344.315 144.559,352.57 149.826,349.992 155.094,352.629 
 160.361,353.807 165.629,357.467 170.896,145.36 176.163,342.748 181.431,344.962 186.698,358.295 191.965,358.297 197.233,355.102 202.5,358.283 207.767,358.297 
 213.035,358.297 218.302,358.295 223.569,358.289 228.837,358.297 234.104,358.297 239.371,358.102 244.639,358.281 249.906,358.167 255.173,353.012 260.441,351.198 
 265.708,358.195 270.976,352.852 276.243,353.863 281.51,332.646 286.778,337.364 292.045,344.478 297.312,326.558 302.58,324.588 307.847,225.038 313.114,298.294 
 318.382,93.6536 323.649,222.155 328.916,316.029 334.184,89.4885 339.451,194.117 344.718,65.8929 349.986,18.1322 355.253,19.7087 360.521,18.1061 365.788,18.1731 
 371.055,48.1696 376.323,21.4288 381.59,20.2364 386.857,23.2382 392.125,19.2112 397.392,22.1803 402.659,20.7572 407.927,19.6674 413.194,21.6321 418.461,21.9186 
 423.729,23.6818 428.996,37.0338 434.263,25.7518 439.531,28.4059 444.798,62.4948 450.066,34.0321 455.333,44.4924 460.6,56.782 465.868,62.7725 471.135,173.902 
 476.402,33.3419 481.67,134.645 486.937,22.41 492.204,72.1926 497.472,54.0506 502.739,77.0965 508.006,75.9119 513.274,106.228 518.541,71.4238 523.808,87.4444 
 529.076,216.123 534.343,115.921 539.61,125.555 544.878,112.513 550.145,162.027 555.413,135.127 560.68,156.108 565.947,158.41 571.215,173.62 576.482,183.768 
 
 "/>
<polyline clip-path="url(#clip02)" style="stroke:#e26f46; stroke-width:1; stroke-opacity:1; fill:none" points="
 55.0141,174.494 60.2815,165.816 65.5488,125.188 70.8162,352.625 76.0835,349.83 81.3509,353.59 86.6182,308.168 91.8856,314.291 97.1529,341.522 102.42,326.06 
 107.688,321.834 112.955,353.021 118.222,355.447 123.49,355.203 128.757,355.014 134.024,347.581 139.292,350.857 144.559,352.674 149.826,353.6 155.094,354.746 
 160.361,355.599 165.629,358.004 170.896,207.596 176.163,344.294 181.431,348.003 186.698,358.297 191.965,358.297 197.233,355.833 202.5,358.293 207.767,358.29 
 213.035,358.297 218.302,358.225 223.569,358.179 228.837,358.138 234.104,358.262 239.371,357.887 244.639,357.96 249.906,357.421 255.173,352.76 260.441,354.183 
 265.708,358.169 270.976,346.157 276.243,347.632 281.51,316.106 286.778,327.674 292.045,329.757 297.312,307.269 302.58,316.502 307.847,230.573 313.114,282.509 
 318.382,125.049 323.649,235.32 328.916,305.914 334.184,77.8153 339.451,183.583 344.718,112.788 349.986,18.3523 355.253,23.7744 360.521,18.1232 365.788,18.4692 
 371.055,118.411 376.323,20.8127 381.59,18.2398 386.857,18.8807 392.125,18.3293 397.392,18.91 402.659,18.4141 407.927,18.2043 413.194,19.2304 418.461,18.8979 
 423.729,19.6072 428.996,34.3397 434.263,19.3166 439.531,18.9212 444.798,35.735 450.066,36.7935 455.333,30.9241 460.6,32.5609 465.868,42.8943 471.135,149.98 
 476.402,20.2068 481.67,103.171 486.937,19.3402 492.204,50.3129 497.472,44.5411 502.739,71.5655 508.006,59.7279 513.274,105.472 518.541,48.4198 523.808,98.609 
 529.076,184.18 534.343,132.946 539.61,139.729 544.878,67.4847 550.145,171.869 555.413,137.69 560.68,165.523 565.947,165.583 571.215,180.107 576.482,185.771 
 
 "/>
<polyline clip-path="url(#clip02)" style="stroke:#3da44d; stroke-width:1; stroke-opacity:1; fill:none" points="
 55.0141,174.494 60.2815,165.816 65.5488,125.188 70.8162,352.625 76.0835,349.83 81.3509,353.59 86.6182,308.168 91.8856,314.291 97.1529,341.522 102.42,326.06 
 107.688,321.834 112.955,353.021 118.222,355.447 123.49,355.203 128.757,355.014 134.024,347.581 139.292,350.857 144.559,352.674 149.826,353